# Study case for renewable power systems
## Loading Packages necessary for simulation¶

In [1]:
using Pkg;
Pkg.instantiate();
cd(@__DIR__);
using PowerDynamics;
using Plots;
using DataFrames;
using OrdinaryDiffEq: ODEProblem, Rodas4, solve;
include("plotting.jl");
include("helpers.jl");
include("simulate_pd.jl");

### Scenario with curtailed power plants

In [2]:
# Model building
node_list=[
    CurtailedPowerPlantWithInertia(P=1,ω_0=2π*50,T_AI=20,K_PPLL=50,K_IPLL=625,T_d=0.0003,T_f=0.0004,K_PV=0.28,K_IV=186), # node 1
    SlackAlgebraic(U=1), #node 2
    CurtailedPowerPlantWithInertia(P=2.5,ω_0=2π*50,T_AI=20,K_PPLL=50,K_IPLL=625,T_d=0.0003,T_f=0.0004,K_PV=0.28,K_IV=186), # node 3
    PQAlgebraic(P=-0.478, Q=-0.0), #node 4
    PQAlgebraic(P=-2.476, Q=-0.016), #node 5
    SwingEqLVS(H=5.06, P=-0.3, D=0.0063662, Ω=314.159, Γ=2, V=1), #node 6
    CurtailedPowerPlantWithInertia(P=2.0,ω_0=2π*50,T_AI=20,K_PPLL=50,K_IPLL=0.5,T_d=0.0003,T_f=0.0004,K_PV=0.28,K_IV=186), # node 7
    SwingEqLVS(H=5.06, P=-0.3, D=0.0063662, Ω=314.159, Γ=2, V=1), #node 8
    PQAlgebraic(P=-0.295,Q= -0.166), #node 9
    PQAlgebraic(P=-0.29, Q=-0.058), #node 10
    PQAlgebraic(P=-0.035,Q= -0.018), #node 11
    PQAlgebraic(P=-0.061, Q=-0.016), #node 12
    PQAlgebraic(P=-0.135, Q=-0.058), #node 13
    PQAlgebraic(P=-0.149, Q=-0.05) #node 14
];

line_list=[
    PiModelLine(from=1, to=2, y=4.99913-15.2631im, y_shunt_km=1/2*0.0528*1im, y_shunt_mk=1/2*0.0528*1im), # line 1
    PiModelLine(from=1, to=5, y=1.0259-4.23498im, y_shunt_km=1/2*0.0492*1im, y_shunt_mk=1/2*0.0492*1im),  # line 2
    PiModelLine(from=2, to=3, y=1.13502-4.78186im, y_shunt_km=1/2*0.0438*1im, y_shunt_mk=1/2*0.0438*1im), # line 3
    PiModelLine(from=2, to=4, y=1.68603-5.11584im, y_shunt_km=1/2*0.0374*1im, y_shunt_mk=1/2*0.0374*1im), # line 4
    PiModelLine(from=2, to=5, y=1.70114-5.19393im, y_shunt_km=1/2*0.034*1im, y_shunt_mk=1/2*0.034*1im), # line 5
    PiModelLine(from=3, to=4, y=1.98598-5.06882im, y_shunt_km=1/2*0.0346*1im, y_shunt_mk=1/2*0.0346*1im), # line 6
    PiModelLine(from=4, to=5, y=6.84098-21.5786im, y_shunt_km=1/2*0.0128*1im, y_shunt_mk=1/2*0.0128*1im), # line 7
    PiModelLine(from=4, to=7, y=0.0-4.78194im, y_shunt_km=0,y_shunt_mk=0), # line 8
    PiModelLine(from=4, to=9, y=0.0-1.79798im, y_shunt_km=0,y_shunt_mk=0), # line 9
    PiModelLine(from=5, to=6, y=0.0-3.96794im, y_shunt_km=0,y_shunt_mk=0), # line 10
    PiModelLine(from=6, to=11,y=1.95503-4.09407im, y_shunt_km=0,y_shunt_mk=0), # line 11
    PiModelLine(from=6, to=12, y=1.52597-3.17596im, y_shunt_km=0,y_shunt_mk=0), # line 12
    PiModelLine(from=6, to=13, y=3.09893-6.10276im, y_shunt_km=0,y_shunt_mk=0), # line 13
    PiModelLine(from=7, to=8, y=0.0-5.67698im, y_shunt_km=0,y_shunt_mk=0), # line 14
    PiModelLine(from=7, to=9, y=0.0-9.09008im, y_shunt_km=0,y_shunt_mk=0), # line 15
    PiModelLine(from=9, to=10, y=3.90205-10.3654im, y_shunt_km=0,y_shunt_mk=0), # line 16
    PiModelLine(from=9, to=14, y=1.42401-3.02905im, y_shunt_km=0,y_shunt_mk=0), # line 17
    PiModelLine(from=10, to=11,y= 1.88088-4.40294im, y_shunt_km=0,y_shunt_mk=0), # line 18
    PiModelLine(from=12, to=13, y=2.48902-2.25197im, y_shunt_km=0,y_shunt_mk=0), # line 19
    PiModelLine(from=13, to=14, y=1.13699-2.31496im, y_shunt_km=0,y_shunt_mk=0) # line 20
];

powergrid = PowerGrid(node_list,line_list)
operationpoint = find_operationpoint(powergrid);

In [6]:
# applying perturbation for the sudden loss of load at the disturbed node
timespan= (0.,5);
tspan_fault = (0.5,5);
disturbed_node=4;
pd = PowerPerturbation(node=disturbed_node,fault_power=0.23, tspan_fault=tspan_fault);

In [8]:
result = simulate(pd,powergrid,operationpoint,timespan);

MethodError: MethodError: no method matching svd(::SparseArrays.SparseMatrixCSC{Float64,Int64}; full=false)
Closest candidates are:
  svd(!Matched::BitArray{2}) at /buildworker/worker/package_linux64/build/usr/share/julia/stdlib/v1.4/LinearAlgebra/src/bitarray.jl:90 got unsupported keyword argument "full"
  svd(!Matched::LinearAlgebra.AbstractTriangular; kwargs...) at /buildworker/worker/package_linux64/build/usr/share/julia/stdlib/v1.4/LinearAlgebra/src/triangular.jl:2631
  svd(!Matched::Union{DenseArray{T,2}, Base.ReinterpretArray{T,2,S,A} where S where A<:Union{SubArray{T,N,A,I,true} where I<:Union{Tuple{Vararg{Real,N} where N}, Tuple{AbstractUnitRange,Vararg{Any,N} where N}} where A<:DenseArray where N where T, DenseArray}, Base.ReshapedArray{T,2,A,MI} where MI<:Tuple{Vararg{Base.MultiplicativeInverses.SignedMultiplicativeInverse{Int64},N} where N} where A<:Union{Base.ReinterpretArray{T,N,S,A} where S where A<:Union{SubArray{T,N,A,I,true} where I<:Union{Tuple{Vararg{Real,N} where N

In [7]:
# running the simulation
sol_pd,result_pd = simulate_pd(pd,powergrid,operationpoint,timespan);

InterruptException: InterruptException:

In [ ]:
plot_res(result_pd,powergrid,disturbed_node);

In [101]:
# calculate RoCoF and nadir
determine_rocof_nadir(powergrid,sol_pd,timespan[2],tspan_fault[1])

5×3 DataFrame
│ Row │ node  │ RoCoF     │ nadir       │
│     │ Int64 │ Float64   │ Float64     │
├─────┼───────┼───────────┼─────────────┤
│ 1   │ 6     │ 1.43512   │ 0.129691    │
│ 2   │ 8     │ 1.56007   │ 0.172435    │
│ 3   │ 3     │ 0.105416  │ 0.00145962  │
│ 4   │ 1     │ 0.129908  │ 0.00452953  │
│ 5   │ 7     │ 0.0155988 │ 0.000515462 │

### Scenario with only type 4 wind power plants

In [95]:
# specific nodes are replaced for scenario with only wind power generation
node_list[1]= WindTurbineGenType4_RotorControl(P=1,T_L=0.0001,ω_0=2π*50,T_H=0.0055,K_ω=50,K_PPLL=10,K_IPLL=625,Q_ref=0,C=1,J=4,ω_rref=1,u_dcref=1,K_Q=0.1,K_v=400,K_pv=10,K_iv=10,K_ptrq=3,K_itrq=0.6);
node_list[3]= WindTurbineGenType4_RotorControl(P=2.5,T_L=0.0001,ω_0=2π*50,T_H=0.0055,K_ω=10,K_PPLL=50,K_IPLL=625,Q_ref=0,C=1,J=4,ω_rref=1,u_dcref=1,K_Q=0.1,K_v=400,K_pv=10,K_iv=10,K_ptrq=3,K_itrq=0.6);
node_list[7]= WindTurbineGenType4_RotorControl(P=2,T_L=0.0001,ω_0=2π*50,T_H=0.0055,K_ω=10,K_PPLL=0.50,K_IPLL=625,Q_ref=0,C=1,J=4,ω_rref=1,u_dcref=1,K_Q=0.1,K_v=400,K_pv=10,K_iv=10,K_ptrq=3,K_itrq=0.6);
# model building
powergrid = PowerGrid(node_list,line_list)
operationpoint = find_operationpoint(powergrid);

# applying perturbation for the sudden loss of load at the disturbed node
timespan= (0.,5);
tspan_fault = (0.5,5);
disturbed_node=4;
pd = PowerPerturbation(node_number=disturbed_node,fraction=0.5, tspan_fault=tspan_fault);
# running the simulation
sol_pd,result_pd = simulate_pd(pd,powergrid,operationpoint,timespan);

plot_res(result_pd,powergrid,disturbed_node);

In [100]:
# calculate RoCoF and nadir
determine_rocof_nadir(powergrid,sol_pd,timespan[2],tspan_fault[1])

5×3 DataFrame
│ Row │ node  │ RoCoF     │ nadir       │
│     │ Int64 │ Float64   │ Float64     │
├─────┼───────┼───────────┼─────────────┤
│ 1   │ 6     │ 1.43512   │ 0.129691    │
│ 2   │ 8     │ 1.56007   │ 0.172435    │
│ 3   │ 3     │ 0.105416  │ 0.00145962  │
│ 4   │ 1     │ 0.129908  │ 0.00452953  │
│ 5   │ 7     │ 0.0155988 │ 0.000515462 │

### Scenario with mix of different renewable power technologies

In [97]:
# specific nodes are replaced for scenario with mix of renewable power generation technologies
node_list[1] = CurtailedPowerPlantWithInertia(P=1,ω_0=2π*50,T_AI=20,K_PPLL=50,K_IPLL=625,T_d=0.0003,T_f=0.0004,K_PV=0.28,K_IV=186);
node_list[3] = WindTurbineGenType4_RotorControl(P=2.5,T_L=0.0001,ω_0=2π*50,T_H=0.0055,K_ω=10,K_PPLL=50,K_IPLL=625,Q_ref=0,C=1,J=4,ω_rref=1,u_dcref=1,K_Q=0.1,K_v=400,K_pv=10,K_iv=10,K_ptrq=3,K_itrq=0.6);
node_list[7] = CurtailedPowerPlantWithInertia(P=2,ω_0=2π*50,T_AI=20,K_PPLL=50,K_IPLL=0.5,T_d=0.0003,T_f=0.0004,K_PV=0.28,K_IV=186);
node_list[14]= CSIMinimal(I_r=0.25);
# model building
powergrid = PowerGrid(node_list,line_list)
operationpoint = find_operationpoint(powergrid);

# applying perturbation for the sudden loss of load at the disturbed node
timespan= (0.,5);
tspan_fault = (0.5,5);
disturbed_node=4;
pd = PowerPerturbation(node_number=disturbed_node,fraction=0.5, tspan_fault=tspan_fault);
# running the simulation
sol_pd,result_pd = simulate_pd(pd,powergrid,operationpoint,timespan);

plot_res(result_pd,powergrid,disturbed_node);

In [99]:
# calculate RoCoF and nadir
determine_rocof_nadir(powergrid,sol_pd,timespan[2],tspan_fault[1])

5×3 DataFrame
│ Row │ node  │ RoCoF     │ nadir       │
│     │ Int64 │ Float64   │ Float64     │
├─────┼───────┼───────────┼─────────────┤
│ 1   │ 6     │ 1.43512   │ 0.129691    │
│ 2   │ 8     │ 1.56007   │ 0.172435    │
│ 3   │ 3     │ 0.105416  │ 0.00145962  │
│ 4   │ 1     │ 0.129908  │ 0.00452953  │
│ 5   │ 7     │ 0.0155988 │ 0.000515462 │